# Import Libraries

In [ ]:
import os

In [ ]:
from tensorflow.keras.models import load_model
import cv2
import numpy as np
import pandas as pd
from collections import deque
from moviepy.editor import *

In [ ]:
# Download Model uncomment if running in Google Colab or Do not have the trained model
#!wget --load-cookies /tmp/cookies.txt "https://docs.google.com/uc?export=download&confirm=$(wget --quiet --save-cookies /tmp/cookies.txt --keep-session-cookies --no-check-certificate 'https://docs.google.com/uc?export=download&id=1vNp1c7ouaWtaHb5GdLZX6OV5ldpXwg_Z' -O- | sed -rn 's/.*confirm=([0-9A-Za-z_]+).*/\1\n/p')&id=1vNp1c7ouaWtaHb5GdLZX6OV5ldpXwg_Z" -O Suspicious_Human_Activity_Detection_VGG16_LSTM_Model.h5 && rm -rf /tmp/cookies.txt

In [ ]:
# # Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# Declare Constants

In [ ]:
# Specify the height and width to which each video frame will be resized in our dataset.
IMAGE_HEIGHT , IMAGE_WIDTH = 64, 64

# Specify the number of frames of a video that will be fed to the model as one sequence.
SEQUENCE_LENGTH = 20

# Specify the directory containing the UCF50 dataset.
DATASET_DIR = "/content/drive/MyDrive/Peliculas"

# Specify the list containing the names of the classes used for training. Feel free to choose any set of classes.
CLASSES_LIST = ["jogging","running","suspicious","walking"]

# Load Model

In [ ]:
model = load_model('/content/drive/MyDrive/Peliculas/Suspicious_Human_Activity_Detection_LRCN_Model.h5')

# Prediction of Single Action

In [ ]:
SEQUENCE_LENGTH = 30


def predict_single_action(video_file_path, SEQUENCE_LENGTH):
    '''
    This function will perform single action recognition prediction on a video using the LRCN model.
    Args:
    video_file_path:  The path of the video stored in the disk on which the action recognition is to be performed.
    SEQUENCE_LENGTH:  The fixed number of frames of a video that can be passed to the model as one sequence.
    '''

    # Initialize the VideoCapture object to read from the video file.
    video_reader = cv2.VideoCapture(video_file_path)

    # Get the width and height of the video.
    original_video_width = int(video_reader.get(cv2.CAP_PROP_FRAME_WIDTH))
    original_video_height = int(video_reader.get(cv2.CAP_PROP_FRAME_HEIGHT))

    # Declare a list to store video frames we will extract.
    frames_list = []

    # Initialize a variable to store the predicted action being performed in the video.
    predicted_class_name = ''

    # Get the number of frames in the video.
    video_frames_count = int(video_reader.get(cv2.CAP_PROP_FRAME_COUNT))

    # Calculate the interval after which frames will be added to the list.
    skip_frames_window = max(int(video_frames_count/SEQUENCE_LENGTH),1)

    # Iterating the number of times equal to the fixed length of sequence.
    for frame_counter in range(SEQUENCE_LENGTH):

        # Set the current frame position of the video.
        video_reader.set(cv2.CAP_PROP_POS_FRAMES, frame_counter * skip_frames_window)

        # Read a frame.
        success, frame = video_reader.read()

        # Check if frame is not read properly then break the loop.
        if not success:
            break

        # Resize the Frame to fixed Dimensions.
        resized_frame = cv2.resize(frame, (IMAGE_HEIGHT, IMAGE_WIDTH))

        # Normalize the resized frame by dividing it with 255 so that each pixel value then lies between 0 and 1.
        normalized_frame = resized_frame / 255

        # Appending the pre-processed frame into the frames list
        frames_list.append(normalized_frame)

    # Passing the  pre-processed frames to the model and get the predicted probabilities.
    predicted_labels_probabilities = model.predict(np.expand_dims(frames_list, axis = 0))[0]

    # Get the index of class with highest probability.
    predicted_label = np.argmax(predicted_labels_probabilities)

    # Get the class name using the retrieved index.
    predicted_class_name = CLASSES_LIST[predicted_label]

    # Display the predicted action along with the prediction confidence.
    print(f'Action Predicted: {predicted_class_name}\nConfidence: {predicted_labels_probabilities[predicted_label]}')

    # Release the VideoCapture object.
    video_reader.release()

In [ ]:
predict_single_action("/content/drive/MyDrive/Peliculas/jogging/person02_jogging_d1_uncomp.avi",SEQUENCE_LENGTH)

1/1 [==============================] - 1s 701ms/step
Action Predicted: running
Confidence: 0.2908494472503662


In [ ]:
predict_single_action("/content/drive/MyDrive/Peliculas/running/person12_running_d4_uncomp.avi",SEQUENCE_LENGTH)

1/1 [==============================] - 0s 54ms/step
Action Predicted: running
Confidence: 0.29656121134757996


In [ ]:
predict_single_action("/content/drive/MyDrive/Peliculas/suspicious/fight_0007.mpeg",SEQUENCE_LENGTH)

1/1 [==============================] - 0s 54ms/step
Action Predicted: running
Confidence: 0.29558873176574707


# All Action Prediction in Video

In [ ]:
def predict_on_video(video_file_path, output_file_path, SEQUENCE_LENGTH):
    '''
    This function will perform action recognition on a video using the LRCN model.
    Args:
    video_file_path:  The path of the video stored in the disk on which the action recognition is to be performed.
    output_file_path: The path where the ouput video with the predicted action being performed overlayed will be stored.
    SEQUENCE_LENGTH:  The fixed number of frames of a video that can be passed to the model as one sequence.
    '''

    # Initialize the VideoCapture object to read from the video file.
    video_reader = cv2.VideoCapture(video_file_path)

    # Get the width and height of the video.
    original_video_width = int(video_reader.get(cv2.CAP_PROP_FRAME_WIDTH))
    original_video_height = int(video_reader.get(cv2.CAP_PROP_FRAME_HEIGHT))

    # Initialize the VideoWriter Object to store the output video in the disk.
    video_writer = cv2.VideoWriter(output_file_path, cv2.VideoWriter_fourcc(*'DIVX'),
                                   video_reader.get(cv2.CAP_PROP_FPS), (original_video_width, original_video_height))

    # Declare a queue to store video frames.
    frames_queue = deque(maxlen = SEQUENCE_LENGTH)

    # Initialize a variable to store the predicted action being performed in the video.
    predicted_class_name = ''

    # Iterate until the video is accessed successfully.
    while video_reader.isOpened():

        # Read the frame.
        ok, frame = video_reader.read()

        # Check if frame is not read properly then break the loop.
        if not ok:
            break

        # Resize the Frame to fixed Dimensions.
        resized_frame = cv2.resize(frame, (IMAGE_HEIGHT, IMAGE_WIDTH))

        # Normalize the resized frame by dividing it with 255 so that each pixel value then lies between 0 and 1.
        normalized_frame = resized_frame / 255

        # Appending the pre-processed frame into the frames list.
        frames_queue.append(normalized_frame)

        # Check if the number of frames in the queue are equal to the fixed sequence length.
        if len(frames_queue) == SEQUENCE_LENGTH:

            # Pass the normalized frames to the model and get the predicted probabilities.
            predicted_labels_probabilities = model.predict(np.expand_dims(frames_queue, axis = 0))[0]

            # Get the index of class with highest probability.
            predicted_label = np.argmax(predicted_labels_probabilities)

            # Get the class name using the retrieved index.
            predicted_class_name = CLASSES_LIST[predicted_label]

        # Write predicted class name on top of the frame.
        cv2.putText(frame, predicted_class_name, (10, 30), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2)

        # Write The frame into the disk using the VideoWriter Object.
        video_writer.write(frame)

    # Release the VideoCapture and VideoWriter objects.
    video_reader.release()
    video_writer.release()

In [ ]:
# Create output directory if it doesn't exist
test_videos_directory = 'test_videos'
os.makedirs(test_videos_directory, exist_ok=True)

# Provide the direct path to the video file from Google Drive
input_video_file_path_drive = '/content/drive/MyDrive/dcsass-dataset/Human-Activity.mp4'

# Construct the output video path
output_video_file_path_drive = f'{test_videos_directory}/Output-SeqLen{SEQUENCE_LENGTH}.mp4'

# Perform Action Recognition on the video from Google Drive
predict_on_video(input_video_file_path_drive, output_video_file_path_drive, SEQUENCE_LENGTH)

# Display the output video
VideoFileClip(output_video_file_path_drive, audio=False, target_resolution=(300, None)).ipython_display()

1/1 [==============================] - 0s 60ms/step
Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4



t:  99%|█████████▉| 886/897 [00:04<00:00, 165.72it/s, now=None]WARNING:py.warnings:/usr/local/lib/python3.10/dist-packages/moviepy/video/io/ffmpeg_reader.py:123: UserWarning: Warning: in file test_videos/Output-SeqLen30.mp4, 337500 bytes wanted but 0 bytes read,at frame 896/897, at time 35.84/35.84 sec. Using the last valid frame instead.
  warnings.warn("Warning: in file %s, "%(self.filename)+

                                                               

Moviepy - Done !
Moviepy - video ready __temp__.mp4


In [ ]:
VideoFileClip(output_video_file_path_drive, audio=False, target_resolution=(300, None)).ipython_display()

Moviepy - Building video __temp__.mp4.
Moviepy - Writing video __temp__.mp4



Moviepy - Done !
Moviepy - video ready __temp__.mp4


In [ ]:
import cv2
from google.colab.patches import cv2_imshow


In [ ]:
# Create a VideoCapture object
cap = cv2.VideoCapture(0)

# Check if the camera is opened correctly
if not cap.isOpened():
    print("Error: Could not open camera.")
else:
    # Capture frame-by-frame
    ret, frame = cap.read()

    # Display the captured frame
    cv2_imshow(frame)

# Release the VideoCapture object
cap.release()


Error: Could not open camera.


In [ ]:
import cv2
import numpy as np
from keras.models import load_model

# Load the trained model
# model = load_model("Suspicious_Human_Activity_Detection_LRCN_Model.h5")

# Define the classes for activities (modify as per your model)
activity_classes = ["Walking", "Running", "Standing", "Sitting", "Watching", "fighting", "fights", "noFight"]

# Parameters for preprocessing
FRAME_COUNT = 30  # Number of frames per sequence
FRAME_HEIGHT = 64  # Height of each frame
FRAME_WIDTH = 64  # Width of each frame

def preprocess_frame(frame):
    # Preprocess the frame (resize, normalize, etc.)
    resized_frame = cv2.resize(frame, (FRAME_WIDTH, FRAME_HEIGHT))
    preprocessed_frame = resized_frame / 255.0  # Normalize pixel values
    return preprocessed_frame

def detect_activity(frames):
    # Preprocess each frame in the sequence
    preprocessed_frames = [preprocess_frame(frame) for frame in frames]

    # Stack frames into a 4D tensor
    input_sequence = np.stack(preprocessed_frames, axis=0)

    # Make predictions using the model
    predictions = model.predict(np.expand_dims(input_sequence, axis=0))

    # Get the predicted activity class
    predicted_class_index = np.argmax(predictions)
    predicted_activity = activity_classes[predicted_class_index]

    return predicted_activity

def capture_and_detect_activity():
    # Open the default camera (usually the webcam)
    cap = cv2.VideoCapture(0)

    # Check if the camera opened successfully
    if not cap.isOpened():
        print("Error: Unable to open camera.")
        return

    frame_buffer = []
    while True:
        # Capture frame-by-frame
        ret, frame = cap.read()

        if not ret:
            print("Error: Unable to capture frame.")
            break

        # Add frame to buffer
        frame_buffer.append(frame)

        # Maintain frame buffer size
        if len(frame_buffer) > FRAME_COUNT:
            frame_buffer.pop(0)

        # Detect human activity when enough frames are collected
        if len(frame_buffer) == FRAME_COUNT:
            activity = detect_activity(frame_buffer)

            # Display the frame with the predicted activity
            cv2.putText(frame, activity, (50, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2, cv2.LINE_AA)
            cv2.imshow('Suspicious Human Activity Detection', frame)

        # Press 'q' to exit the loop
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

    # Release the capture
    cap.release()
    cv2.destroyAllWindows()

# Call the function to start capturing and detecting activity
capture_and_detect_activity()

Error: Unable to open camera.
